In [1]:
#Setting up all necessary libraries
import matplotlib.pyplot as plt 
%config InlineBackend.figure_format = 'retina' 
import numpy as np 
from skimage import io  
%matplotlib osx

In [2]:
# Used for Debugging
def PrintArrayInfo(a): 
    print("Array info:") 
    print("shape:", a.shape) 
    print("dtype:", a.dtype) 
    print("min, max:", a.min(), a.max()) 

## Creating Simulated Landscape 

In [3]:
from image_manipulation import prepare_landsat_image 
bands = [6,5,2]  
ls_false = prepare_landsat_image(bands) 


fig, ax = plt.subplots(1, 1, figsize=(10, 10)) 
plt.axis('off') 
plt.imshow(ls_false) 
plt.show() 

In [4]:
from PIL import Image 
from image_manipulation import bar_plot_with_colors 
from skimage import img_as_ubyte, img_as_uint, img_as_float64 


#Having it reduced
imageRGB = Image.fromarray(img_as_ubyte(ls_false)) 
 
imageIndexed = imageRGB.quantize(colors=7, kmeans=1) 
rgbFromIndexed = imageIndexed.convert("RGB")
checkfor = rgbFromIndexed.getcolors()
counts = []
palette=[]
labels = []

for i in range(7):
    counts.append(checkfor[i][0])
    palette.append(checkfor[i][1])
    labels.append(i)

     
bar_plot_with_colors(counts,palette,labels) 

In [5]:
newimg = np.asarray(rgbFromIndexed)

In [6]:
plt.subplots(1, 1, figsize=(10, 10))
test = newimg[2000:2250,2000:2250]
plt.imshow(test) 
plt.show() 

## Creating Prediction Bins 

In [7]:
from datetime import datetime
from meteostat import Point, Daily

# Set time period
start = datetime(2021, 6, 15)
end = datetime(2021, 11, 15)

# Create Point for Selected Point
location = Point(38.93551246083111, -120.73146615558441)

# Get daily data for Fire Season Data
data = Daily(location, start, end)
data = data.fetch()


# Plot line chart including average, minimum and maximum temperature
data.plot(y=['tavg', 'tmin', 'tmax'])
plt.ylabel("Degrees(C)")
plt.show()

In [8]:
# data.plot(y=['prcp', 'wdir', 'wspd'])
data.plot(y=['wdir'])
plt.ylabel("Rotation Degrees")
plt.show()

In [9]:
data.plot(y=['prcp'])
plt.ylabel("Inches or Rain")
plt.show()

In [10]:
data.plot(y=['wspd'])
plt.ylabel("Windspeed(miles)")
plt.show()

## Simulation

In [11]:
#Have to index the it according to previpus array
simulatedarray = np.asarray(imageIndexed)[2000:2250,2000:2250]

In [12]:
#FINDING COLOR INDEXES

np.unique(simulatedarray,return_counts=True)
#COLORS INDEX
#0 = LIGHT-GREY YES
#1 = TAN ROCK YES
#2 = LIGHT-GREY (MED VEGITATION) YES
#3 = LOW VEGITATION YES
#4 = DARK-GREY YES
#5 = HIGH VEGITATION YES
#6 = WATER YES


(array([0, 1, 2, 3, 4, 5, 6], dtype=uint8),
 array([  833,  3005, 13642,  5301,  3500, 27126,  9093]))

In [51]:
import matplotlib.colors as col

#SET-UP
#Creating Custom Color Map for Animation
custom_cmap = col.ListedColormap(["lightgrey","tan","limegreen","darkolivegreen","dimgrey","forestgreen","darkslategrey","darkred","orangered","peru"])

burnable = [5,2,3] #Pixel Index to tell which is burnable

burned = [7,8] #Pixel Index to tell which is already burned

burning = [] #Array or currently burning pixels

tester = np.copy(simulatedarray)

maxX = tester.shape[0]
maxY = tester.shape[1]    

#Used to create first inital starting point
def createStartingPoint():
    
    
    startx = np.random.randint(0,maxX)
    starty = np.random.randint(0,maxY)
    
    while (tester[startx,starty] not in burnable):

        startx = np.random.randint(0,maxX)
        starty = np.random.randint(0,maxY)
        
    #Have to do this for color map to load correctly
    tester[startx,starty] = 7
    burning.append([[startx,starty],7])

    if (startx + 2 < maxX):
        tester[startx + 1,starty] = 8
        burning.append([[startx+1,starty],8])
        tester[startx + 2,starty] = 9
    else: 
        tester[startx - 1,starty] = 8
        burning.append([[startx-1,starty],8])
        tester[startx - 2,starty] = 9
        
#Used to find direction to place pixel in
def chooseDirection(coords):
    
    x = coords[0]
    y = coords[1]
    ind = np.random.randint(0, len(data['wdir']))
    newdir = data['wdir'][ind]
    spd = data['wspd'][ind]
    adder = 1
    if spd <=8 and spd > 6:
        adder = 2
    if spd <=10 and spd > 8:
        adder = 3
    if spd <=12 and spd > 10:
        adder = 3
    if spd <=14 and spd > 12:
        adder = 4
    if spd <=16 and spd > 14:
        adder = 4
    if spd > 16:
        adder = 4
    if newdir <= 45:
        newcoords = [x+adder,y]
    if newdir <= 90 and newdir > 45:
        newcoords = [x+adder,y+adder]
    if newdir <= 135 and newdir > 90:
        newcoords = [x,y+adder]
    if newdir <= 180 and newdir > 135:
        newcoords = [x-adder,y+adder]
    if newdir <= 225 and newdir > 180:
        newcoords = [x-adder,y]
    if newdir <= 270 and newdir > 225:
        newcoords = [x-adder,y-adder]
    if newdir <= 315 and newdir > 270:
        newcoords = [x,y-adder]
    if newdir <= 360 and newdir > 315:
        newcoords = [x+adder,y-adder]
    
    return newcoords 

def chooseNumofParticles(start,end):
    #Select random day from conditions to simulate
    n = 30
    ind = np.random.randint(start, end)
    temp = data['tavg'][ind]
    rain = data['prcp'][ind]

    
    #Higher temps means more particles to sample
    if temp <= 20:
        n += 10
    if temp <= 30 and temp > 20:
        n += 20
    if temp <= 30 and temp > 30:
        n += 30
    
    #If lots of rain don't sample a particle.
    if rain > 2:
        n -= 10
    if rain > 5:
        n = 0
        
    return n


def setToFire(coords):
    x = coords[0]
    y = coords[1]
    if ((0 < x < tester.shape[0]) and (0 < y < tester.shape[1]) and tester[x,y] in burnable):
        pixel = tester[x,y]
        if pixel == burnable[0]:
            tester[coords[0],coords[1]] = 7
            burning.append([[x,y],7])
            
        #Mid Vegetation
        if pixel == burnable[1]:
            tester[coords[0],coords[1]] = 8
            burning.append([[x,y],8])
            
        #Low Vegetation
        if pixel == burnable[2]:
            tester[coords[0],coords[1]] = 9
            burning.append([[x,y],9])
    return

#Function that advances current fires burning
def advanceFires():
    to_remove = []
    for i in range(len(burning)):
        fire = burning[i]
        if fire[1] <= 8 :
            daCoords = fire[0]
            da_x = daCoords[0]
            da_y = daCoords[1]
            tester[da_x,da_y] = 8
            fire[1] += 0.1
        if fire[1] <= 9 and fire[1] > 8:
            daCoords = fire[0]
            da_x = daCoords[0]
            da_y = daCoords[1]
            tester[da_x,da_y] = 9
            fire[1] += 0.2
        if fire[1] <= 10 and fire[1] > 9:
            daCoords = fire[0]
            da_x = daCoords[0]
            da_y = daCoords[1]
            tester[da_x,da_y] = 9
            fire[1] += 0.4
        if fire[1] >= 9:
            to_remove.append(fire)
    for fir in to_remove:
        burning.remove(fir)

    return
    
    
    

In [61]:
burning = []
tester = np.copy(simulatedarray)

createStartingPoint()
print(burning)

# plt.imshow(tester, cmap=custom_cmap) 
# plt.show()

[[[191, 13], 7], [[192, 13], 8]]


In [62]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Test', artist='Hector',comment='Test.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

In [63]:
with writer.saving(fig, "Presentation.mp4", dpi=200):

    days = 140
#     plt.draw() 
#     plt.pause(0.05) 
#     writer.grab_frame() 
    
    for i in range(0,days):
        
        if (i != 0):
            advanceFires()

        currlen = len(burning)

        if (currlen== 0):
            break


        #samling over week of temps.
        parts = chooseNumofParticles(i,i+7)
        for p in range(parts):
            rindex = np.random.randint(0,len(burning))
            source = burning[rindex][0]
            pixel = chooseDirection(source)
            setToFire(pixel)
        
        plt.clf() 
        plt.imshow(tester, cmap=custom_cmap) 
        plt.show()  
        plt.pause(0.05) 
        writer.grab_frame()  
        
# plt.imshow(tester, cmap=custom_cmap) 
# plt.show()      
    
